In [1]:
import h5py
import pickle
import pandas as pd

In [2]:
f = h5py.File('array_index.h5py', 'r')

In [3]:
list(f.keys())[:10]

['dim',
 'index_doc_id_100',
 'index_doc_id_1000',
 'index_doc_id_10000',
 'index_doc_id_10001',
 'index_doc_id_10002',
 'index_doc_id_10003',
 'index_doc_id_10004',
 'index_doc_id_10005',
 'index_doc_id_10007']

In [9]:
f['dim'][()]

14980

In [4]:
ids = set([x.split("_")[-1] for x in f.keys() if x != "dim"])

In [5]:
from collections import defaultdict

In [6]:
from tqdm import tqdm

In [7]:
passages = defaultdict(dict)

for i in tqdm(ids):
    passage_idx = f[f"index_doc_id_{i}"][:]
    values = f[f"index_doc_value_{i}"][:]
    for ip, p in enumerate(passage_idx):
        passages[str(p)][i] = float(values[ip])

100%|██████████| 14980/14980 [00:05<00:00, 2505.42it/s]


In [8]:
len(passages)

8519

In [10]:
import json

In [17]:
with open("dense_passages.json", "w") as fp:
    json.dump(passages , fp)

In [11]:
f = open("dense_passages.json")

passages = json.load(f)

# Heirarrchical

In [12]:
# this part might be wrong - the weights for the passages need to be sparse or keyed if dense

# array of arrays of dense terms weights for each passage
array = []

for passage in passages:
    # array of term weights for each passage
    sub_array = []
    for key in passages[passage]:
        sub_array.append(passages[passage][key])
    array.append(sub_array)

In [3]:
import pandas as pd

In [18]:
df = pd.DataFrame(array)
df2 = df.fillna(0)

In [53]:
sparse_weights_frame = pd.DataFrame(passages).T

In [54]:
sparse_weights_frame

2396      7857      2076      2056      2024      4613      2111  \
94     0.247593  0.033599  0.244491  0.050646  0.261035  0.265997  1.327136   
102    0.678590       NaN       NaN       NaN       NaN       NaN       NaN   
103    0.678590       NaN       NaN       NaN       NaN       NaN       NaN   
114    0.062892       NaN       NaN       NaN       NaN       NaN       NaN   
115    0.032396       NaN       NaN       NaN       NaN       NaN       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
4193        NaN       NaN       NaN       NaN       NaN       NaN       NaN   
5647        NaN       NaN       NaN       NaN       NaN       NaN       NaN   
1929        NaN       NaN       NaN       NaN       NaN       NaN       NaN   
431         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
65527       NaN       NaN       NaN       NaN       NaN       NaN       NaN   

          16924      6040      6256  ...  14174  9136  18214  10711  10770  \
94     0.298036  0.039324  0.270001  ...    NaN   NaN    NaN    NaN    NaN   
102         NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
103         NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
114         NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
115         NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
...         ...       ...       ...  ...    ...   ...    ...    ...    ...   
4193        NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
5647        NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
1929        NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
431         NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   
65527       NaN       NaN       NaN  ...    NaN   NaN    NaN    NaN    NaN   

       16168  9577     23942     11639     18410  
94       NaN   NaN       NaN       NaN       NaN  
102      NaN   NaN       NaN       NaN       NaN  
103      NaN   NaN       NaN       NaN       NaN  
114      NaN   NaN       NaN       NaN       NaN  
115      NaN   NaN       NaN       NaN       NaN  
...      ...   ...       ...       ...       ...  
4193     NaN   NaN       NaN       NaN       NaN  
5647     NaN   NaN  0.728822  0.701943  1.589865  
1929     NaN   NaN       NaN       NaN       NaN  
431      NaN   NaN       NaN       NaN       NaN  
65527    NaN   NaN       NaN       NaN       NaN  

[8520 rows x 14980 columns]

In [55]:
from scipy.spatial.distance import pdist

In [ ]:
def sparse_similarity(s1, s2):
    s3 = {}
    for k, v in s1.items():
        s3[k] = s2.get(k, 0) * v
    return sum(s3.values())

In [58]:
sorted_passages = sorted(list(passages.items()), key=lambda x: x[0])

In [65]:
def make_sparse(dense_rep, size_collection):
    zeros = np.zeros(size_collection, dtype=np.float32)
    for k, v in dense_rep.items():
        zeros[int(k)] = v
    return zeros

In [67]:
sorted_passages_values = np.array([make_sparse(x[1], 30522) for x in sorted_passages])

In [69]:
dist_matrix = pdist(sorted_passages_values, metric='cosine')

In [72]:
# save to file
with open('dist_matrix.npy', 'wb') as f:
    np.save(f, dist_matrix)

In [73]:
# load from file
with open('dist_matrix.npy', 'rb') as f:
    dist_matrix = np.load(f)

In [79]:
dist_matrix = np.nan_to_num(dist_matrix)

In [83]:
# Heirarchical Ordering
from scipy.cluster import hierarchy
Z = linkage(dist_matrix, method='ward')
sorted_passages_keys = np.array([x[0] for x in sorted_passages])
order = pd.DataFrame(hierarchy.leaves_list(hierarchy.optimal_leaf_ordering(Z, dist_matrix)))

In [87]:
order.to_csv("order_sparse.csv")

In [88]:
order.head()

0
0  1174
1  6489
2  2319
3  2323
4  2277

# Making The Tree

In [92]:
odered = pd.read_csv('order_sparse.csv')

In [93]:
this_order = list(odered['this_column'])

In [94]:
this_order = [str(i) for i in this_order]
this_order

['1174',
 '6489',
 '2319',
 '2323',
 '2277',
 '2325',
 '2278',
 '2116',
 '6519',
 '2841',
 '3699',
 '1087',
 '4469',
 '2927',
 '2440',
 '6992',
 '6053',
 '6052',
 '1955',
 '7007',
 '1175',
 '2839',
 '3697',
 '2840',
 '2704',
 '5616',
 '1529',
 '2610',
 '6308',
 '2160',
 '5815',
 '7237',
 '5386',
 '6309',
 '1995',
 '1781',
 '1407',
 '1408',
 '4825',
 '6674',
 '1153',
 '1885',
 '3243',
 '3284',
 '4692',
 '4101',
 '3249',
 '8084',
 '662',
 '4021',
 '1005',
 '2491',
 '63',
 '4391',
 '6307',
 '6311',
 '2439',
 '1409',
 '4823',
 '1783',
 '3674',
 '6658',
 '7147',
 '2641',
 '2767',
 '5185',
 '6741',
 '309',
 '1987',
 '6125',
 '2359',
 '523',
 '5440',
 '1401',
 '5348',
 '6175',
 '6339',
 '2705',
 '5888',
 '7541',
 '8408',
 '7519',
 '8244',
 '6497',
 '3036',
 '3033',
 '5838',
 '23',
 '3614',
 '6490',
 '2542',
 '62',
 '2275',
 '217',
 '6491',
 '4301',
 '4290',
 '6310',
 '4023',
 '3486',
 '3485',
 '1950',
 '3996',
 '3997',
 '3999',
 '1951',
 '4000',
 '7877',
 '2861',
 '3427',
 '1067',
 '3452',
 '

In [95]:
ordered_dict = {key: passages[key] for key in this_order if key in passages}

In [96]:
ordered_dict

{'1174': {'2662': 0.2989622950553894,
  '13109': 0.19452695548534393,
  '7467': 0.002988755237311125,
  '3295': 0.6294912099838257,
  '5841': 0.39735788106918335,
  '14763': 1.3329094648361206,
  '5334': 1.5127429962158203,
  '10300': 0.43953078985214233,
  '13024': 0.8494231700897217,
  '15680': 0.8955181837081909,
  '3749': 0.05836432799696922,
  '5848': 0.5726537108421326,
  '7664': 2.980792284011841,
  '5298': 0.03668598830699921,
  '6745': 0.1763903647661209,
  '5086': 0.9697846174240112,
  '8124': 0.27059632539749146,
  '2783': 0.6166603565216064,
  '11194': 0.24319754540920258,
  '3573': 0.20481084287166595,
  '2525': 0.22061340510845184,
  '3309': 0.08990366756916046,
  '17207': 1.7364810705184937,
  '4825': 0.3533141016960144,
  '2472': 0.1166946217417717,
  '2136': 0.0039200144819915295,
  '2194': 0.4708186388015747,
  '9065': 0.11755571514368057,
  '8809': 0.33552372455596924,
  '2902': 0.2734430134296417,
  '2533': 0.2939874529838562,
  '16155': 0.004845899064093828,
  '136

In [97]:
import math
import numpy as np
import functools
from copy import deepcopy

In [98]:
def sparse_max(s1, s2):
    s3 = deepcopy(s2)
    for k, v in s1.items():
        s3[k] = max(s2.get(k, 0), v)
    return s3

def sparse_similarity(s1, s2):
    s3 = {}
    for k, v in s1.items():
        s3[k] = s2.get(k, 0) * v
    return sum(s3.values())

In [99]:
def next_smallest_power_of_2(x: int) -> int:
    """Get the next smallest power of 2

    Args:def sparse_max(s1, s2):
    s3 = deepcopy(s2)
    for k, v in s1.items():
        s3[k] = max(s2.get(k, 0), v)
    return s3

def sparse_similarity(s1, s2):
    s3 = {}
    for k, v in s1.items():
        s3[k] = s2.get(k, 0) * v
    return sum(s3.values())
        x (int)
    
    Result:
        next smallest power of 2 from x
    """
    exponent = math.floor(math.log2(x))
    return 2**exponent

In [112]:
def make_tree(array, min_bucket_size=100, func=...):
    """Make balanced binary tree with a minimum bucket size

    Aggregate using the given function
    """
    number_of_buckets = math.ceil(len(array) / min_bucket_size)
    balanced_number_bottom_buckets = next_smallest_power_of_2(number_of_buckets)
    bottom_bucket_size = math.ceil(len(array) / balanced_number_bottom_buckets)

    #TODO: you still need to store the indices of the underlying array 
    # associated with each aggregate score
    bottom_buckets = [
        functools.reduce(func, array[i:i+bottom_bucket_size]) 
        for i in range(0, len(array), bottom_bucket_size)]
    
    tree = {}
    bottom_level = int(np.log2(balanced_number_bottom_buckets))
    tree[bottom_level] = bottom_buckets
    bucks = bottom_buckets
    level = bottom_level - 1
    while len(bucks) > 2:
        b = [
                functools.reduce(func, bucks[i:i+1])
                for i in range(0, len(bucks), 2)
            ]
        tree[level] = b
        bucks = b
        level-=1
    
    return tree

In [101]:
def get_result(query, tree, max_depth=None):
    level = min(tree.keys())
    index = 0
    if not max_depth:
        max_depth = len(tree.keys())

    while (level in tree) and max_depth > 0:
        left = tree[level][index]
        right = tree[level][index+1]
        go_left = sparse_similarity(left, query) > sparse_similarity(right, query)
        index = index*2 if go_left else index*2+1
        level+=1
        max_depth-=1
    
    final_level = level-1
    return index, final_level

In [102]:
passage_list = list(ordered_dict.items())

In [103]:
sorted_passage_list = sorted(passage_list, key=lambda x: x[0])

In [104]:
len(sorted_passage_list)

8519

In [105]:
# the order of the passages
sorted_passage_index_dense = [v[0] for v in sorted_passage_list]

In [106]:
import pickle
with open("passage_index_order", "wb") as fp:   #Pickling
    pickle.dump(sorted_passage_index_dense, fp)

In [107]:
sorted_passage_dense = [v[1] for v in sorted_passage_list]

In [113]:
binary_tree = make_tree(sorted_passage_dense, min_bucket_size=100, func=sparse_max)

In [114]:
with open("binary_tree_scores.json", "w") as fp:
    json.dump(binary_tree , fp)

In [115]:
binary_tree

{6: [{'3965': 0.1936878263950348,
   '3710': 1.574418544769287,
   '4031': 0.23249311745166779,
   '2756': 0.3888832926750183,
   '4228': 2.0257458686828613,
   '3590': 0.24719080328941345,
   '10733': 2.2234292030334473,
   '6243': 0.6718361973762512,
   '3976': 1.9471088647842407,
   '6959': 1.2719762325286865,
   '2036': 1.2135322093963623,
   '2172': 0.20224814116954803,
   '11825': 0.4406713843345642,
   '18909': 2.324401617050171,
   '4825': 1.248598575592041,
   '2116': 0.7943254709243774,
   '8116': 1.0818424224853516,
   '3963': 0.525521993637085,
   '1997': 1.033021330833435,
   '2654': 0.7652298808097839,
   '8808': 2.2049427032470703,
   '2382': 2.4415876865386963,
   '2028': 0.6968080401420593,
   '9485': 0.21328014135360718,
   '5359': 1.5070438385009766,
   '25609': 1.6991550922393799,
   '2932': 0.4342394173145294,
   '3538': 0.8115280866622925,
   '11345': 1.1250231266021729,
   '6085': 0.4374257028102875,
   '3556': 0.21919289231300354,
   '3013': 0.864228367805481,
 

In [116]:
for k,v in binary_tree.items():
    print(k, len(v))

6 64
5 32
4 16
3 8
2 4
1 2


In [91]:
res = get_result(sorted_passage_dense[0], binary_tree)

In [92]:
res

(0, 7)

In [125]:
q = sorted_passage_dense[2]  # use the first passage as a dummy query
max_depth = 7
res_index, lev = get_result(q, binary_tree, max_depth)
bucket_size = math.ceil(len(sorted_passage_dense) / len(binary_tree[lev]))
bucket_start = bucket_size*res_index
bucket_end = bucket_size*(res_index+1)

In [126]:
bucket_start

66898

In [127]:
bucket_end

69056

In [128]:
res_passages = sorted_passage_dense[bucket_start:bucket_end]

In [129]:
tree_scores = [sparse_similarity(r, q) for r in res_passages]
tree_loc = np.argmax(tree_scores) + bucket_start

In [130]:
tree_loc

67030

In [131]:
# look up the passage index
sorted_passage_index_dense[tree_loc]

'160323'

In [132]:
sorted_passage_index_dense[:5]

['0', '1', '10', '100', '1000']